# Mine XGM Data and LPD Profile #

Author: S. Hauf, Version: 0.1

In [ ]:
dc = [1.5, 1] # center offset
geometry_file = "/gpfs/exfel/d/cal/exchange/lpdMF_00.h5" # the geometry file to use, MAR 2018
proposal_folder = "/gpfs/exfel/exp/FXE/201701/p002045/proc/" # folder under which runs can be found
xgm_folder = "/gpfs/exfel/exp/FXE/201701/p002045/raw/" # folder under which runs can be found
adc_folder = "/gpfs/exfel/exp/FXE/201701/p002045/raw/" # folder under which runs can be found
file_prefix = "CORR-R{:04d}-LPD" # prefix of each data file - should be a template to replace run number
raw_prefix = "RAW-R{:04d}-LPD" # prefix of each data file - should be a template to replace run number
xgm_prefix = "RAW-R{:04d}-DA03" # prefix for XGM file - should be a template to replace run number
adc_prefix = "RAW-R{:04d}-DA01" # prefix for ADC file - should be a template to replace run number
data_path = "INSTRUMENT/FXE_DET_LPD1M-1/DET/{}CH0:xtdf/image/data" # path to data in file
gain_path = "INSTRUMENT/FXE_DET_LPD1M-1/DET/{}CH0:xtdf/image/gain" # path to data in file
xgm_path = "/INSTRUMENT/SA1_XTD2_XGM/DOOCS/MAIN:output/data/intensityTD" # path to XGM data
xgm_path_td = "/INSTRUMENT/SA1_XTD2_XGM/DOOCS/MAIN:output/data/intensityAUXTD" # path to XGM AUX data
adc_root = "/INSTRUMENT/FXE_RR_DAQ/ADC/1:network/digitizers" # root path to ADC data
adc_paths = ["channel_1_A/apd/pulseIntegral", "channel_1_B/apd/pulseIntegral",
             "channel_1_C/apd/pulseIntegral", "channel_1_D/apd/pulseIntegral"]
temp_out_folder = "/gpfs/exfel/data/scratch/haufs/test/tempout6"
cluster_profile = "noDB"
chunk_size = 512 # read this amount of data at once
runs = "69-72"
method = "average" # method to use for evaluation of images: radial, average

sequences = [-1] # range allowed

In [ ]:
def create_run_list(proposal_folder, file_prefix, xgm_folder, xgm_prefix, runs):
    import glob

    from cal_tools.tools import parse_runs
    in_runs = parse_runs(runs, return_type=int)
    runs_to_process = []
    for r in in_runs:
        
        try:
            
            tl = glob.glob("{}/r{:04d}/{}*.h5".format(proposal_folder, r, file_prefix.format(r)))
            tlxgm = glob.glob("{}/r{:04d}/{}*.h5".format(xgm_folder, r, xgm_prefix.format(r)))
            
            if len(tl) and len(tlxgm):
                runs_to_process.append(r)
        except Exception as e:
            print(e)
            pass
        
    return runs_to_process

In [ ]:
import warnings

warnings.filterwarnings('ignore')
import os

import h5py
import matplotlib
import numpy as np

matplotlib.use("agg")
import matplotlib.pyplot as plt

%matplotlib inline
from functools import partial

from ipyparallel import Client

print("Connecting to profile {}".format(cluster_profile))
view = Client(profile=cluster_profile)[:]
view.use_dill()

d_quads = [(-14+dc[0],-300+dc[1]),(10+dc[0],-9+dc[1]),(-256+dc[0],15+dc[1]),(-280+dc[0],-276+dc[1])] # MAR 2018
#runs_to_process = create_run_list(proposal_folder, file_prefix, xgm_folder, xgm_prefix, runs)
runs_to_process = runs

if method not in ["radial", "average"]:
    print("Unknown method, defaulting to average")
    method = "average"

In [ ]:
def get_sequences(in_folder, run, sequences):
    import glob
    import re

    import numpy as np
    
    sequence_files = glob.glob("{}/r{:04d}/*-S*.h5".format(in_folder, run))
    seq_nums = set()
    for sf in sequence_files:
        seqnum = re.findall(r".*-S([0-9]*).h5", sf)[0]
        seq_nums.add(int(seqnum))
    if len(sequences) and sequences[0] != -1:
        seq_nums &= set(sequences)
   
    return list(seq_nums)

In [ ]:
def handle_sequence(run, proposal_folder, xgm_folder,
                    file_prefix, xgm_prefix, data_path, xgm_path, xgm_path_td, raw_prefix, 
                    geometry_file, d_quads, temp_out_folder, gain_path, 
                    adc_folder, adc_prefix, adc_root, adc_paths, method, sequence):
    import cal_tools.metrology as metro
    import h5py
    import numpy as np
    from scipy.stats import binned_statistic_2d

    # convert the Carthesian coordinates of the detector to polar coordinates
    def mod_cart_to_pol(d, dx, dy, filter_by_val=True):
        """ Convert carthesian coords to polar coords
        """
        cx, cy = d.shape
        x = np.arange(cx)+dx
        y = np.arange(cy)+dy
        x = np.repeat(x[:,None], cy, axis=1)
        y = np.repeat(y[None,:], cx, axis=0)

        rho = np.sqrt(x**2 + y**2).flatten()
        phi = np.arctan2(y, x).flatten()
        flat = d.flatten()

        # we also perform a bit of filtering here

        if filter_by_val:
            good = np.isfinite(flat) & (flat > 0) & (flat < 1e5)

            return rho[good], phi[good], flat[good], good

        return rho, phi, flat, None
    
    
    
    xgm_file = "{}/r{:04d}/{}-S{:05d}.h5".format(xgm_folder, run, xgm_prefix.format(run), sequence)
    adc_file = "{}/r{:04d}/{}-S{:05d}.h5".format(adc_folder, run, adc_prefix.format(run), sequence) if adc_folder != "none" else None
    data_files = "{}/r{:04d}/{}*-S{:05d}.h5".format(proposal_folder, run, file_prefix.format(run), sequence)
    raw_files = "{}/r{:04d}/{}*-S{:05d}.h5".format(xgm_folder, run, raw_prefix.format(run), sequence)
    
    try:
        with h5py.File(xgm_file, "r") as f:

            xgm_tid = np.array(f["/INDEX/trainId"])

            adc_datas = []
            if adc_file:
                with h5py.File(adc_file, "r") as f2:
                    adc_tid = np.array(f2["/INDEX/trainId"])
                    intersected = np.intersect1d(xgm_tid, adc_tid)
                    adc_idx = np.in1d(adc_tid, intersected)
                    xgm_idx = np.in1d(xgm_tid, intersected)
                    for p in adc_paths:
                        print("ADC path: {}".format("{}/{}".format(adc_root, p)))
                        adc_datas.append(f2["{}/{}".format(adc_root, p)][adc_idx, ...])

                    xgm_tid = xgm_tid[xgm_idx]
                    xgm_d = np.array(f[xgm_path])[xgm_idx]
                    xgm_d_td = np.array(f[xgm_path_td])[xgm_idx]
            else:

                xgm_d = np.array(f[xgm_path])
                xgm_d_td = np.array(f[xgm_path_td])

            if method == "radial":
                posarr, intersected, pcounts = metro.positionFileList(data_files, data_path, geometry_file, d_quads, trainIds=xgm_tid)
                garr, _, _ = metro.positionFileList(data_files, gain_path, geometry_file, d_quads, trainIds=xgm_tid)
                rawarr, _, _ = metro.positionFileList(raw_files, data_path, geometry_file, d_quads, trainIds=xgm_tid, nwa=True, max_counts=16)
            elif method == "average":
                posarr, intersected, pcounts = metro.matchedFileList(data_files, data_path, trainIds=xgm_tid)
                garr, _, _ = metro.matchedFileList(data_files, gain_path, trainIds=xgm_tid)
                rawarr, _, _ = metro.matchedFileList(raw_files, data_path, trainIds=xgm_tid, nwa=True, max_counts=63)
                rawarr = np.moveaxis(rawarr, 3, 4)
            print(posarr.shape)
            xgm_d = xgm_d[np.in1d(xgm_tid, intersected), ...]
            xgm_d_td = xgm_d_td[np.in1d(xgm_tid, intersected), ...]
            xgm_f = []
            xgm_f_td = []
            adc_datas_f = []
            for i in range(len(adc_datas)):
                adc_datas_f.append([])
            for i in range(pcounts.size):
                xgm_f += xgm_d[i, :pcounts[i]].flatten().tolist()
                xgm_f_td += xgm_d_td[i, :pcounts[i]].flatten().tolist()
                for k in range(len(adc_datas)):
                    adc_datas_f[k] += adc_datas[k][i, :pcounts[i]].flatten().tolist()
            xgm_d = np.array(xgm_f)
            xgm_f_td = np.array(xgm_f_td)
            for i in range(len(adc_datas)):
                adc_datas[i] = np.array(adc_datas_f[i])
            xgm_res = []
            xgm_res_td = []
            max_im = []
            sum_im = []
            max_gain = []
            mean_gain = []
            raw_det = []
            adc_ret = []
            for i in range(len(adc_datas)):
                adc_ret.append([])
            print("Processing {} images, XGM size: {}, ADC size: {}".format(posarr.shape[0], xgm_d.size, adc_datas[0].size))
            print("Data shape {}, {}".format(posarr.shape, rawarr.shape))
            for i in range(posarr.shape[0] if method=="radial" else posarr.shape[-1]):

                xgm = xgm_d[i]
                adc = []
                for k, a in enumerate(adc_datas):
                    adc_ret[k].append(a[i])

                xgm_res.append(xgm)
                xgm_res_td.append(xgm_f_td[i])
                if method == "radial":
                    im = posarr[i, ...]                
                    # Here we create histograms of the data in a polar coordinate system.
                    # We use numpys hist2d function, giving it the polar coordinates of 
                    # each pixels, and weighing that coordinate with the pixel's value.
                    # We obtain a histogram for each module, according to its position defined
                    # in the coord_list.

                    hs = []
                    bins_nums = []
                    edges = []

                    goods = []
                    bins = 1000

                    dx, dy = -750, -750

                    rho, phi, weights, good = mod_cart_to_pol(im, dy, dx, False)

                    h, phi_edges, rho_edges, bns = binned_statistic_2d(phi, rho, weights, bins=(bins,bins),
                                                                           range=((-np.pi, np.pi), (0, 1000)),
                                                                           statistic = "mean")
                    bins_nums.append(bns)
                    hs.append(h)
                    edges.append((phi_edges, rho_edges))
                    goods.append(good)

                    x = np.arange(bins)/bins*1000*500e-6
                    y = np.arange(bins)/bins*2.
                    ds = np.nansum(np.array(hs),axis=0)
                    ds[ds == 0] = np.nan
                    profile = np.nanmedian(ds, axis=0)

                    max_im.append(np.nanmax(profile))
                    sum_im.append(np.nansum(profile))
                    max_idx = np.nanargmax(profile)

                    hs = []
                    bins_nums = []
                    edges = []

                    goods = []
                    bins = 1000

                    dx, dy = -750, -750

                    rho, phi, weights, good = mod_cart_to_pol(garr[i,...], dy, dx, False)

                    h, phi_edges, rho_edges, bns = binned_statistic_2d(phi, rho, weights, bins=(bins,bins),
                                                                           range=((-np.pi, np.pi), (0, 1000)),
                                                                           statistic = "mean")


                    bins_nums.append(bns)
                    hs.append(h)
                    edges.append((phi_edges, rho_edges))
                    goods.append(good)

                    x = np.arange(bins)/bins*1000*500e-6
                    y = np.arange(bins)/bins*2.
                    ds = np.nansum(np.array(hs),axis=0)
                    ds[ds == 0] = np.nan
                    profile = np.nanmean(ds, axis=0)

                    max_gain.append(profile[max_idx])
                    mean_gain.append(np.nanmean(profile))

                    hs = []
                    bins_nums = []
                    edges = []

                    goods = []
                    bins = 1000

                    dx, dy = -750, -750

                    rho, phi, weights, good = mod_cart_to_pol(rawarr[i,...], dy, dx, False)

                    h, phi_edges, rho_edges, bns = binned_statistic_2d(phi, rho, weights, bins=(bins,bins),
                                                                           range=((-np.pi, np.pi), (0, 1000)),
                                                                           statistic = "mean")
                    bins_nums.append(bns)
                    hs.append(h)
                    edges.append((phi_edges, rho_edges))
                    goods.append(good)

                    x = np.arange(bins)/bins*1000*500e-6
                    y = np.arange(bins)/bins*2.
                    ds = np.nansum(np.array(hs),axis=0)
                    ds[ds == 0] = np.nan
                    profile = np.nanmedian(ds, axis=0)

                    raw_det.append(np.nanmax(profile))

                elif method == "average":

                    im = posarr[..., i]
                    max_im.append(np.nanmedian(im))
                    sum_im.append(np.nansum(im))

                    max_gain.append(np.nanmean(garr[..., i]))
                    mean_gain.append(np.nanmean(garr[..., i]))
                    
                    raw_det.append(np.nanmedian(rawarr[..., i]))
    
        np.savez("{}/{}_{}".format(temp_out_folder, run, sequence),
                 np.array(xgm_res), np.array(max_im), np.array(sum_im),
                 np.array(max_gain), np.array(mean_gain), np.array(xgm_res_td),
                 np.array(raw_det), np.array(adc_ret))
    except:
        pass

In [ ]:
for run in runs_to_process:
    seqs = get_sequences(proposal_folder, run, sequences)
    par_handle = partial(handle_sequence, run, proposal_folder, xgm_folder,
                         file_prefix, xgm_prefix, data_path, xgm_path, xgm_path_td, raw_prefix,
                         geometry_file, d_quads, temp_out_folder, gain_path,
                         adc_folder, adc_prefix, adc_root, adc_paths, method)
    #ret = view.map_sync(par_handle, seqs)
    ret = list(map(par_handle, seqs))